# Collect Data Komentar Youtube Rewind Indonesia 2020 dengan Google Client API 

In [1]:
# !pip install pandas
# !pip install google-api-python-client

In [2]:
# Mengimpor library yang dibutuhkan
import googleapiclient.discovery
import googleapiclient.errors
from pymongo import MongoClient
import time
from dotenv import load_dotenv
import os

In [3]:
# Memuat value dari file .env
load_dotenv()

key = os.getenv('API_KEY_1')
mongodb_url = os.getenv('URL_SANDY')
local_url = os.getenv('URL_LOCAL')

In [4]:
videoID = "LhYfsKc0_tA"

# Mengambil Komentar Dari Youtube dan Langsung Tersimpan pada MongoDB

In [5]:
# Menentukan parameter yang diperlukan, seperti nama layanan API dan versi, serta kunci pengembang
api_service_name = "youtube"
api_version = "v3"
DEVELOPER_KEY = key

# Membangun klien YouTube dengan menggunakan kunci pengembang
youtube = googleapiclient.discovery.build(
    api_service_name, api_version, developerKey=DEVELOPER_KEY
)

# Koneksi ke MongoDB
client = MongoClient(mongodb_url)
db = client["analisisSentimenYTRewind"]
collection = db["collectData2020"]
state_collection = db["state"]

# Menginisialisasi variabel yang akan digunakan
video_id = videoID
max_results = 50  # menetapkan jumlah maksimum komentar yang diambil dalam satu permintaan API, mengurangi jumlah maksimum hasil untuk mengurangi kemungkinan timeout

# Mengambil token halaman berikutnya dari database atau mulai dari awal jika tidak ada
state_doc = state_collection.find_one({"video_id": video_id})
next_page_token = state_doc['next_page_token'] if state_doc else None

#Menyimpan token halaman berikutnya ke dalam database setelah setiap halaman komentar berhasil diambil.
def save_state(video_id, next_page_token):
    """Simpan token halaman berikutnya ke database."""
    state_collection.update_one(
        {"video_id": video_id},
        {"$set": {"next_page_token": next_page_token}},
        upsert=True
    )

#Mengambil balasan dari komentar utama. Setiap balasan ditandai sebagai balasan (is_reply = True)
#dan disimpan ke database jika belum ada.
def get_replies(parent_id):
    """Mengambil balasan untuk komentar tertentu."""
    replies = []
    next_page_token_replies = None

    while True:
        response_replies = youtube.comments().list(
            part="snippet",
            parentId=parent_id,
            maxResults=max_results,
            pageToken=next_page_token_replies
        ).execute()

        for reply in response_replies['items']:
            reply['snippet']['is_reply'] = True  # Menandai komentar ini sebagai balasan
            retries = 3  # Jumlah maksimal percobaan ulang
            while retries > 0:
                try:
                    # Cek apakah balasan sudah ada di database
                    if not collection.find_one({"id": reply['id']}):
                        collection.insert_one(reply['snippet'])
                    break  # Keluar dari loop ulang jika berhasil
                except errors.AutoReconnect as e:
                    print(f"AutoReconnect error: {e}, retrying...")
                    retries -= 1
                    time.sleep(5)  # Tunggu beberapa detik sebelum mencoba lagi
            replies.append(reply['snippet'])

        next_page_token_replies = response_replies.get('nextPageToken')
        if not next_page_token_replies:
            break

    return replies

while True:  # Loop ini akan terus berjalan sampai tidak ada halaman komentar berikutnya yang tersedia
    try:
        # Mengirim permintaan untuk mendapatkan komentar
        request = youtube.commentThreads().list(
            part="snippet,replies",
            videoId=video_id,
            maxResults=max_results,  # Jumlah maksimum komentar yang diambil dalam satu permintaan
            pageToken=next_page_token  # Token halaman berikutnya yang digunakan untuk mendapatkan halaman komentar berikutnya
        )
        response = request.execute()  # Menjalankan permintaan dan menyimpan respons dari API ke dalam variabel response

        counter = 1
        # Menyimpan informasi komentar ke dalam list
        for item in response['items']:  # Mengambil daftar komentar dari respons API
            comment = item['snippet']['topLevelComment']['snippet']
            comment['is_reply'] = False  # Menandai komentar ini sebagai komentar utama
            retries = 3  # Jumlah maksimal percobaan ulang
            while retries > 0:
                try:
                    # Cek apakah komentar sudah ada di database
                    if not collection.find_one({"id": item['id']}):
                        collection.insert_one(comment)
                    break  # Keluar dari loop ulang jika berhasil
                except errors.AutoReconnect as e:
                    print(f"AutoReconnect error: {e}, retrying...")
                    retries -= 1
                    time.sleep(5)  # Tunggu beberapa detik sebelum mencoba lagi
            print(f"{counter}: {comment}")
            counter += 1

            # Mengambil balasan dari komentar utama
            if 'replies' in item:
                for reply in item['replies']['comments']:
                    reply_comment = reply['snippet']
                    reply_comment['is_reply'] = True  # Menandai komentar ini sebagai balasan
                    retries = 3  # Jumlah maksimal percobaan ulang
                    while retries > 0:
                        try:
                            # Cek apakah balasan sudah ada di database
                            if not collection.find_one({"id": reply['id']}):
                                collection.insert_one(reply_comment)
                            break  # Keluar dari loop ulang jika berhasil
                        except errors.AutoReconnect as e:
                            print(f"AutoReconnect error: {e}, retrying...")
                            retries -= 1
                            time.sleep(5)  # Tunggu beberapa detik sebelum mencoba lagi
                    print(f"  Reply: {reply_comment}")

        # Simpan state setelah setiap halaman diambil
        next_page_token = response.get('nextPageToken')
        save_state(video_id, next_page_token)

        # Memeriksa apakah ada halaman komentar berikutnya
        if not next_page_token:
            break

    except googleapiclient.errors.HttpError as e:
        if e.resp.status == 404:
            print(f"Video dengan ID {video_id} tidak ditemukan.")
            break
        elif e.resp.status in [500, 502, 503, 504]:
            print("Server error occurred, retrying in 5 seconds...")
            time.sleep(5)
            continue
        else:
            print(f"An HTTP error {e.resp.status} occurred: {e.content}")
            break
    except googleapiclient.errors.Error as e:
        print(f"An error occurred: {e}")
        break
    except TimeoutError as e:
        print("Timeout occurred, retrying in 5 seconds...")
        time.sleep(5)  # Tunggu beberapa detik sebelum mencoba lagi
        continue

print("Komentar berhasil diambil dan disimpan ke MongoDB")


1: {'channelId': 'UC-z1ubmS-iHMVr83EEwRS2g', 'videoId': 'LhYfsKc0_tA', 'textDisplay': 'Keren banget sih ini , ini nih editornya pnya idea bguss ginii .', 'textOriginal': 'Keren banget sih ini , ini nih editornya pnya idea bguss ginii .', 'authorDisplayName': '@tikapuuu', 'authorProfileImageUrl': 'https://yt3.ggpht.com/tAdDZfhForKfNuk79fzuCLBGgzAvrvPHcC5vbJYnHB5zsSF2cl0TDyxkCe8YQQE2X5_VCUlQ=s48-c-k-c0x00ffffff-no-rj', 'authorChannelUrl': 'http://www.youtube.com/@tikapuuu', 'authorChannelId': {'value': 'UCDec5ilXztMiXF5Z7848Q1w'}, 'canRate': True, 'viewerRating': 'none', 'likeCount': 1, 'publishedAt': '2021-11-06T13:45:32Z', 'updatedAt': '2021-11-06T13:45:32Z', 'is_reply': False, '_id': ObjectId('66644cbac80f77a74c86152f')}
2: {'channelId': 'UC-z1ubmS-iHMVr83EEwRS2g', 'videoId': 'LhYfsKc0_tA', 'textDisplay': 'Abis liat chandra di TNS bilang dia lagi yg direct ytr 2021', 'textOriginal': 'Abis liat chandra di TNS bilang dia lagi yg direct ytr 2021', 'authorDisplayName': '@vetriyanti8819', 